# Eat Safe, Love

## Notebook Set Up

In [98]:
# Import dependencies
from pymongo import MongoClient
from pprint import pprint
import pandas as pd

In [99]:
# Create an instance of MongoClient
mongo = MongoClient(port=27017)

In [100]:
# assign the uk_food database to a variable name
db = mongo['uk_food']

In [101]:
# review the collections in our database
print(db.list_collection_names())

['establishments']


In [102]:
# assign the collection to a variable
establishments = db['establishments']

## Part 3: Exploratory Analysis
Unless otherwise stated, for each question: 
* Use `count_documents` to display the number of documents contained in the result.
* Display the first document in the results using `pprint`.
* Convert the result to a Pandas DataFrame, print the number of rows in the DataFrame, and display the first 10 rows.

### 1. Which establishments have a hygiene score equal to 20?

In [103]:
# Find the establishments with a hygiene score of 20
query = {'scores.Hygiene': 20}

# Use count_documents to display the number of documents in the result
results = establishments.find(query)
print(f'There are {db.establishments.count_documents(query)} establishments with a hygiene score of 20')

print('------------------------------------------------------------')
# Display the first document in the results using pprint

pprint(results[0])
    


There are 41 establishments with a hygiene score of 20
------------------------------------------------------------
{'AddressLine1': '5-6 Southfields Road',
 'AddressLine2': 'Eastbourne',
 'AddressLine3': 'East Sussex',
 'AddressLine4': '',
 'BusinessName': 'The Chase Rest Home',
 'BusinessType': 'Caring Premises',
 'BusinessTypeID': 5,
 'ChangesByServerID': 0,
 'Distance': 4613.888288172291,
 'FHRSID': 110681,
 'LocalAuthorityBusinessID': '4029',
 'LocalAuthorityCode': '102',
 'LocalAuthorityEmailAddress': 'Customerfirst@eastbourne.gov.uk',
 'LocalAuthorityName': 'Eastbourne',
 'LocalAuthorityWebSite': 'http://www.eastbourne.gov.uk/foodratings',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'BN21 1BU',
 'RatingDate': '2021-09-23T00:00:00',
 'RatingKey': 'fhrs_0_en-gb',
 'RatingValue': 0,
 'RightToReply': '',
 'SchemeType': 'FHRS',
 '_id': ObjectId('64979bb5667ad5b134bd871f'),
 'geocode': {'latitude': 50.769705, 'longitude': 0.27694},
 'links': [{'href': 'https://api.ratings.f

In [104]:
# Convert the result to a Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict = results[0]
columns = list(inputdict.keys())
values_list = list(inputdict.values())
#converting list to DataFrame
establishments_df = pd.DataFrame(values_list,columns)
# Display the number of rows in the DataFrame
print(f'There are {len(establishments_df.index)} rows in the DataFrame')
print('------------------------------------------------------')
# Display the first 10 rows of the DataFrame
establishments_df.head(10)

There are 28 rows in the DataFrame
------------------------------------------------------


0
_id                       64979bb5667ad5b134bd871f
FHRSID                                      110681
ChangesByServerID                                0
LocalAuthorityBusinessID                      4029
BusinessName                   The Chase Rest Home
BusinessType                       Caring Premises
BusinessTypeID                                   5
AddressLine1                  5-6 Southfields Road
AddressLine2                            Eastbourne
AddressLine3                           East Sussex

### 2. Which establishments in London have a `RatingValue` greater than or equal to 4?

In [130]:
# Find the establishments with London as the Local Authority and has a RatingValue greater than or equal to 4.
query_02 = {'LocalAuthorityName': 'City of London Corporation','RatingValue':{'$gte':4}}
results_02 = establishments.find(query)


# Use count_documents to display the number of documents in the result
print('------------------------------------------------------')

print(f'There are  {establishments.count_documents(query_02)} documents in the results with London as the \
      Local Authority and have a RatingValue greater than or equal to 4 ')

print('------------------------------------------------------')
# Display the first document in the results using pprint
print('Here is the first document in the results')
print('------------------------------------------------------')
pprint(results_02[0])

------------------------------------------------------
There are  33 documents in the results with London as the       Local Authority and have a RatingValue greater than or equal to 4 
------------------------------------------------------
Here is the first document in the results
------------------------------------------------------
{'AddressLine1': 'Oak Apple Farm Building 103 Sheernes Docks',
 'AddressLine2': 'Sheppy Kent',
 'AddressLine3': '',
 'AddressLine4': '',
 'BusinessName': "Charlie's",
 'BusinessType': 'Other catering premises',
 'BusinessTypeID': 7841,
 'ChangesByServerID': 0,
 'Distance': 4627.439467780196,
 'FHRSID': 621707,
 'LocalAuthorityBusinessID': 'PI/000025307',
 'LocalAuthorityCode': '508',
 'LocalAuthorityEmailAddress': 'publicprotection@cityoflondon.gov.uk',
 'LocalAuthorityName': 'City of London Corporation',
 'LocalAuthorityWebSite': 'http://www.cityoflondon.gov.uk/Corporation/homepage.htm',
 'NewRatingPending': False,
 'Phone': '',
 'PostCode': 'ME12',
 'R

In [158]:
# Convert the result to a Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict_02 = results_02[0]
columns_02 = list(inputdict_02.keys())
values_list_02 = list(inputdict_02.values())
#converting list to DataFrame
establishments_df_02 = pd.DataFrame(values_list_02,columns_02)

# Display the number of rows in the DataFrame
print(f'There are {len(establishments_df_02.index)} rows in the DataFrame')
print('------------------------------------------------------')
# Display the first 10 rows of the DataFrame
establishments_df_02.head(10)

There are 28 rows in the DataFrame
------------------------------------------------------


0
_id                                         64979bb6667ad5b134bda13b
FHRSID                                                        621707
ChangesByServerID                                                  0
LocalAuthorityBusinessID                                PI/000025307
BusinessName                                               Charlie's
BusinessType                                 Other catering premises
BusinessTypeID                                                  7841
AddressLine1              Oak Apple Farm Building 103 Sheernes Docks
AddressLine2                                             Sheppy Kent
AddressLine3

### 3. What are the top 5 establishments with a `RatingValue` rating value of 5, sorted by lowest hygiene score, nearest to the new restaurant added, "Penang Flavours"?

In [160]:
# Search within 0.01 degree on either side of the latitude and longitude.
# Rating value must equal 5
# Sort by hygiene score

degree_search = 0.01
latitude = establishments.find({'BusinessName':'Penang Flavours'},{'geocode.latitude':1})
longitude = establishments.find({'BusinessName':'Penang Flavours'},{'geocode.longitude':1})

for lat in latitude:
    #print(lat['geocode']['latitude'] +.01)
    latitude_upper = lat['geocode']['latitude'] +0.1
    latitude_lower = lat['geocode']['latitude'] - 0.1
for lon in longitude:
    longitude_upper = lon['geocode']['longitude'] +0.1
    longitude_lower = lon['geocode']['longitude'] - 0.1

# write query for RatingValue and distance query
query = {'$match':{
    'RatingValue': 5,
    'geocode.latitude': {'$gte': latitude_lower, '$lte': latitude_upper},
    'geocode.longitude': {'$gte': longitude_lower, '$lte': longitude_upper}
}}
                
# Create a dictionary that will allow the pipeline to sort by count in descending order
sort = {'$sort': {'scores.Hygiene': -1}}

# Put the pipeline together
pipeline = [
    query,sort
    
]
                          
# Run the pipeline through the aggregate method and save the results to a variable
results_03 = list(establishments.aggregate(pipeline))
# Print the results
pprint(results_03)
                                         

[{'AddressLine1': 'Christ Church Centre',
  'AddressLine2': 'Kingswood Avenue',
  'AddressLine3': 'Swanley',
  'AddressLine4': 'KENT',
  'BusinessName': 'Swanley Kindergarten Pre-school',
  'BusinessType': 'Caring Premises',
  'BusinessTypeID': 5,
  'ChangesByServerID': 0,
  'Distance': 4640.311011978085,
  'FHRSID': 647170,
  'LocalAuthorityBusinessID': '14/00041/MIXED/S',
  'LocalAuthorityCode': '187',
  'LocalAuthorityEmailAddress': 'environmental.health@sevenoaks.gov.uk',
  'LocalAuthorityName': 'Sevenoaks',
  'LocalAuthorityWebSite': 'http://www.sevenoaks.gov.uk/',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'BR8 8AN',
  'RatingDate': '2022-03-14T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb7667ad5b134bdc483'),
  'geocode': {'latitude': 51.39568, 'longitude': 0.182274},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/647170',
             'rel': 'self'}],
  'm

 {'AddressLine1': '47 High Street',
  'AddressLine2': 'Chislehurst',
  'AddressLine3': '',
  'AddressLine4': '',
  'BusinessName': 'The Broadwick (formally Richoux)',
  'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'ChangesByServerID': 0,
  'Distance': 4645.328973466932,
  'FHRSID': 996412,
  'LocalAuthorityBusinessID': '17/00218/MIXED',
  'LocalAuthorityCode': '505',
  'LocalAuthorityEmailAddress': 'food@bromley.gov.uk',
  'LocalAuthorityName': 'Bromley',
  'LocalAuthorityWebSite': 'http://www.bromley.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'BR7 5AF',
  'RatingDate': '2019-09-04T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb8667ad5b134bdd7d6'),
  'geocode': {'latitude': 51.418016, 'longitude': 0.067328},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/996412',
             'rel': 'self'}],
  'meta': {'dataSource': None,
          

 {'AddressLine1': '',
  'AddressLine2': '258-262 Heathway',
  'AddressLine3': '',
  'AddressLine4': 'Dagenham',
  'BusinessName': 'Iceland',
  'BusinessType': 'Retailers - supermarkets/hypermarkets',
  'BusinessTypeID': 7840,
  'ChangesByServerID': 0,
  'Distance': 4646.768048223893,
  'FHRSID': 122391,
  'LocalAuthorityBusinessID': '5092',
  'LocalAuthorityCode': '501',
  'LocalAuthorityEmailAddress': 'foodsafety@lbbd.gov.uk',
  'LocalAuthorityName': 'Barking and Dagenham',
  'LocalAuthorityWebSite': 'http://www.lbbd.gov.uk/Pages/Home.aspx',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'RM10 9NT',
  'RatingDate': '2020-10-31T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb8667ad5b134bdde15'),
  'geocode': {'latitude': 51.537917, 'longitude': 0.148449},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/122391',
             'rel': 'self'}],
  'meta': {'dataSource': None,

 {'AddressLine1': '11 Anglesea Road',
  'AddressLine2': '',
  'AddressLine3': 'Woolwich',
  'AddressLine4': 'Greenwich',
  'BusinessName': 'Lebanese gourmet',
  'BusinessType': 'Takeaway/sandwich shop',
  'BusinessTypeID': 7844,
  'ChangesByServerID': 0,
  'Distance': 4647.902709657696,
  'FHRSID': 1274355,
  'LocalAuthorityBusinessID': '13704',
  'LocalAuthorityCode': '511',
  'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
  'LocalAuthorityName': 'Greenwich',
  'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'SE18 6EG',
  'RatingDate': '2020-09-22T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bde423'),
  'geocode': {'latitude': 51.4886309, 'longitude': 0.0676794},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1274355',
             'rel': 'self'}],
  'meta': {'dataSource': None,
  

 {'AddressLine1': '',
  'AddressLine2': '205-209 Longbridge Road',
  'AddressLine3': '',
  'AddressLine4': 'Barking',
  'BusinessName': 'East London Bus & Coach Co. Ltd',
  'BusinessType': 'Restaurant/Cafe/Canteen',
  'BusinessTypeID': 1,
  'ChangesByServerID': 0,
  'Distance': 4649.0789225838935,
  'FHRSID': 443037,
  'LocalAuthorityBusinessID': '138594',
  'LocalAuthorityCode': '526',
  'LocalAuthorityEmailAddress': 'themis.skouros@redbridge.gov.uk',
  'LocalAuthorityName': 'Redbridge',
  'LocalAuthorityWebSite': 'http://www.redbridge.gov.uk/',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'IG11 8UE',
  'RatingDate': '2021-05-27T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bde907'),
  'geocode': {'latitude': 51.546622, 'longitude': 0.093749},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/443037',
             'rel': 'self'}],
  'meta': {'dataSource': N

  'AddressLine3': 'Greenwich',
  'AddressLine4': '',
  'BusinessName': 'Kola Butchers',
  'BusinessType': 'Retailers - other',
  'BusinessTypeID': 4613,
  'ChangesByServerID': 0,
  'Distance': 4650.082777630002,
  'FHRSID': 1214390,
  'LocalAuthorityBusinessID': '13238',
  'LocalAuthorityCode': '511',
  'LocalAuthorityEmailAddress': 'health@royalgreenwich.gov.uk',
  'LocalAuthorityName': 'Greenwich',
  'LocalAuthorityWebSite': 'http://www.royalgreenwich.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'SE10 9TZ',
  'RatingDate': '2020-02-27T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdedf5'),
  'geocode': {'latitude': 51.48486, 'longitude': 0.0041473},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1214390',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
    

  'PostCode': 'E13 9AR',
  'RatingDate': '2020-12-03T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdf30e'),
  'geocode': {'latitude': 51.536745, 'longitude': 0.035126},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1250632',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'extractDate': '0001-01-01T00:00:00',
           'itemCount': 0,
           'pageNumber': 0,
           'pageSize': 0,
           'returncode': None,
           'totalCount': 0,
           'totalPages': 0},
  'scores': {'ConfidenceInManagement': 5, 'Hygiene': 5, 'Structural': 0}},
 {'AddressLine1': '230 Strone Road',
  'AddressLine2': 'Manor Park',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'Iced Bubble Tea',
  'BusinessType': 'Other catering premises',
  'BusinessTypeID': 7841,
  'ChangesByServerID': 0,
  'Distance': 4650.85729343701,
  'FHRSID': 14

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'AddressLine1': 'ExCel',
  'AddressLine2': '1 Western Gateway',
  'AddressLine3': 'Canning Town',
  'AddressLine4': 'London',
  'BusinessName': 'Sandwich And Co',
  'BusinessType': 'Takeaway/sandwich shop',
  'BusinessTypeID': 7844,
  'ChangesByServerID': 0,
  'Distance': 4650.098093215453,
  'FHRSID': 1091260,
  'LocalAuthorityBusinessID': '18/00544/FOOD',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E16 1XL',
  'RatingDate': '2019-03-13T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdee19'),
  'geocode': {'latitude': 51.50817, 'longitude': 0.027108},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/1091260',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'e

 {'AddressLine1': '510 - 512 Romford Road',
  'AddressLine2': 'Forest Gate',
  'AddressLine3': 'London',
  'AddressLine4': '',
  'BusinessName': 'City Sweet Centre',
  'BusinessType': 'Retailers - other',
  'BusinessTypeID': 4613,
  'ChangesByServerID': 0,
  'Distance': 4651.095157879672,
  'FHRSID': 869967,
  'LocalAuthorityBusinessID': '74760/0510/0/000',
  'LocalAuthorityCode': '525',
  'LocalAuthorityEmailAddress': 'food@newham.gov.uk',
  'LocalAuthorityName': 'Newham',
  'LocalAuthorityWebSite': 'https://www.newham.gov.uk',
  'NewRatingPending': False,
  'Phone': '',
  'PostCode': 'E7 8AF',
  'RatingDate': '2018-07-26T00:00:00',
  'RatingKey': 'fhrs_5_en-gb',
  'RatingValue': 5,
  'RightToReply': '',
  'SchemeType': 'FHRS',
  '_id': ObjectId('64979bb9667ad5b134bdf490'),
  'geocode': {'latitude': 51.548127, 'longitude': 0.039902},
  'links': [{'href': 'http://api.ratings.food.gov.uk/establishments/869967',
             'rel': 'self'}],
  'meta': {'dataSource': None,
           'ext

In [161]:
# Convert result to Pandas DataFrame
#Creating list from keys and values in dictionary results
inputdict_03 = results_03[0]
columns_03 = list(inputdict_03.keys())
values_list_03 = list(inputdict_03.values())
#converting list to DataFrame
establishments_df_03 = pd.DataFrame(values_list_03,columns_03)

establishments_df_03.head(10)

0
_id                              64979bb7667ad5b134bdc483
FHRSID                                             647170
ChangesByServerID                                       0
LocalAuthorityBusinessID                 14/00041/MIXED/S
BusinessName              Swanley Kindergarten Pre-school
BusinessType                              Caring Premises
BusinessTypeID                                          5
AddressLine1                         Christ Church Centre
AddressLine2                             Kingswood Avenue
AddressLine3                                      Swanley

### 4. How many establishments in each Local Authority area have a hygiene score of 0?

In [ ]:
# Create a pipeline that: 
# 1. Matches establishments with a hygiene score of 0
# 2. Groups the matches by Local Authority
# 3. Sorts the matches from highest to lowest

# Print the number of documents in the result

# Print the first 10 results


In [ ]:
# Convert the result to a Pandas DataFrame

# Display the number of rows in the DataFrame

# Display the first 10 rows of the DataFrame
